# Titanic

In [289]:
import warnings
warnings.filterwarnings('ignore')
import operator, functools, time, itertools
import tensorflow as tf
import numpy as np
from sklearn.metrics import roc_curve, auc, accuracy_score, precision_score, recall_score, f1_score
import pandas as pd
from sklearn.preprocessing import StandardScaler, Imputer
from sklearn.model_selection import train_test_split
from sklearn.utils import shuffle
import matplotlib.pyplot as plt
import hashlib

In [290]:
def titanic_dataset():
    dataset = pd.read_csv("data\\Titanic.csv")
    del dataset["name"]
    del dataset["cabin"]
    del dataset["ticket"]
    del dataset["home.dest"]
    del dataset["body"]
    del dataset["boat"]
    
    for column in ["age", "sibsp", "parch", "fare"]:
        imp = Imputer()
        dataset[column] = imp.fit_transform(dataset[column].values.reshape(-1,1))
    
    dataset["sibsp"] =  dataset["sibsp"].astype(float)
    dataset = pd.get_dummies(dataset, columns=["sex", "embarked"], prefix=["sex", "embarked"])
    
    need_scaling = ["pclass","age", "sibsp", "parch", "fare"]
    scaler = StandardScaler()
    for feature in need_scaling:
        dataset[feature] = scaler.fit_transform(dataset[feature].values.reshape(-1,1))

    return dataset

dataset = titanic_dataset()
#print("Dataset shape:", dataset.shape)
#print("Survived rate:\n", dataset['survived'].value_counts())

In [291]:
dataset_good = dataset[dataset['survived'] == 1]
dataset_bad = dataset[dataset['survived'] == 0]
del dataset_good['survived']
del dataset_bad['survived']

print("Dataset_good shape:", dataset_good.shape)
print("Dataset_bad shape:", dataset_bad.shape)

good_rate = 500/1309
bad_rate = 809/1309
print("Survived rate:", good_rate)
print("Deceased rate:", bad_rate)

Dataset_good shape: (500, 10)
Dataset_bad shape: (809, 10)
Survived rate: 0.3819709702062643
Deceased rate: 0.6180290297937356


#### Stratificirana podjela - provjera koliko je potrebno "dobrih" i "loših" primjera u train i test setu. Sampliranje.

In [292]:
train_size = 1009
test_size = 300
print("Number of survived for train:", round(train_size*good_rate))
print("Number of deceased for train:", round(train_size*bad_rate))
print("Number of survived for test:", round(test_size*good_rate))
print("Number of deceased for test:", round(test_size*bad_rate))

good_train, good_test = train_test_split(dataset_good, test_size=0.20)
bad_train, bad_test = train_test_split(dataset_bad, test_size=0.20)
print("\nDimensions for symmetric classifier:")
print(good_train.shape, good_test.shape, bad_train.shape, bad_test.shape)

y_train = np.array([1]*len(good_train) + [0]*len(bad_train)).reshape(-1,1)
x_train = good_train.append(bad_train)
x_train['survived'] = y_train
x_train = shuffle(x_train)
y_train = x_train['survived'].reshape(-1,1)
del x_train['survived']

y_test = np.array([1]*len(good_test) + [0]*len(bad_test)).reshape(-1,1)
x_test = good_test.append(bad_test)
x_test['survived'] = y_test
x_test = shuffle(x_test)
y_test = x_test['survived'].reshape(-1,1)
del x_test['survived']

print("\nDimensions for base classifier:")
print(x_train.shape, y_train.shape, x_test.shape, y_test.shape)

Number of survived for train: 385
Number of deceased for train: 624
Number of survived for test: 115
Number of deceased for test: 185

Dimensions for symmetric classifier:
(400, 10) (100, 10) (647, 10) (162, 10)

Dimensions for base classifier:
(1047, 10) (1047, 1) (262, 10) (262, 1)


## Neural network

In [293]:
def small_network(input_placeholder):
    layer_1 = tf.layers.dense(input_placeholder, 70, tf.nn.relu, name="layer_1", reuse=tf.AUTO_REUSE)
    layer_2 = tf.layers.dense(layer_1, 60, tf.nn.relu, name="layer_2", reuse=tf.AUTO_REUSE)
    layer_3 = tf.layers.dense(layer_2, 40, tf.nn.relu, name="layer_3", reuse=tf.AUTO_REUSE)
    layer_4 = tf.layers.dense(layer_3, 30, tf.nn.relu, name="layer_4", reuse=tf.AUTO_REUSE)
    layer_5 = tf.layers.dense(layer_4, 15, tf.nn.relu, name="layer_5", reuse=tf.AUTO_REUSE)
    output = tf.layers.dense(layer_5, 1, name="output", reuse=tf.AUTO_REUSE)
    return output

In [294]:
def metrics(y_out, y_test):
    y_out = [o >= 0.5 for o in y_out]
    print('\nAccuracy score = ', accuracy_score(y_test, y_out))
    print('Precision score = ', precision_score(y_test, y_out))
    print('Recall score = ', recall_score(y_test, y_out))
    print('F1 score = ', f1_score(y_test, y_out))

### Base classifier

In [295]:
tf.reset_default_graph()

input_ = tf.placeholder(tf.float32, shape=[None, x_train.shape[1]])
output = tf.placeholder(tf.float32, shape=[None,1])

logit = small_network(input_)
h = tf.sigmoid(logit)

loss = tf.losses.sigmoid_cross_entropy(output, logit)
lr = tf.placeholder(tf.float32, shape=[])
train_op = tf.train.AdamOptimizer(learning_rate=lr, beta1=0.9, beta2=0.999).minimize(loss)

In [296]:
base_hashmap = {}

def base_classification(data, y, l_r, num_epochs, num_batches, if_test):
    bsize = len(data) // num_batches
    losses = []
    for epoch in range(num_epochs):
        total_loss = 0.0
        h_out = []
        
        for batch in range(num_batches):
            i = batch * bsize
            j = (batch + 1) * bsize
            
            loss_, h_, _ = sess.run([loss, h, train_op],feed_dict={input_: data.iloc[i:j,:],output: y[i:j],lr:l_r})
            h_out.extend([hh[0] for hh in h_])
            total_loss += loss_
            
            if(if_test):
                for k in range(i,j):
                    x = data.iloc[k,:]
                    key = hashlib.sha512(x.values.tobytes()).hexdigest()
                    base_hashmap[key] = tuple((x, round(h_out[k])))

        losses.append(total_loss / num_batches)
        print("Epoch {} / {}, Loss = {}".format(epoch + 1, num_epochs, total_loss / num_batches))
        
    return h_out, losses

In [323]:
with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    
    print("Training...")
    base_train_out, losses = base_classification(x_train, y_train, 0.0001, 10000, 1, False)
    metrics(base_train_out, y_train)
    
    print("\nTesting...")
    base_test_out, losses = base_classification(x_test, y_test, 0.0001, 1, 1, True) 
    metrics(base_test_out, y_test)

Training...
Epoch 1 / 10000, Loss = 0.7041496634483337
Epoch 2 / 10000, Loss = 0.703220784664154
Epoch 3 / 10000, Loss = 0.702296793460846
Epoch 4 / 10000, Loss = 0.7013864517211914
Epoch 5 / 10000, Loss = 0.70048987865448
Epoch 6 / 10000, Loss = 0.6996055245399475
Epoch 7 / 10000, Loss = 0.6987319588661194
Epoch 8 / 10000, Loss = 0.6978694200515747
Epoch 9 / 10000, Loss = 0.6970131993293762
Epoch 10 / 10000, Loss = 0.6961552500724792
Epoch 11 / 10000, Loss = 0.695303738117218
Epoch 12 / 10000, Loss = 0.6944507956504822
Epoch 13 / 10000, Loss = 0.6936013102531433
Epoch 14 / 10000, Loss = 0.6927564740180969
Epoch 15 / 10000, Loss = 0.6919171810150146
Epoch 16 / 10000, Loss = 0.6910848021507263
Epoch 17 / 10000, Loss = 0.6902588605880737
Epoch 18 / 10000, Loss = 0.6894397139549255
Epoch 19 / 10000, Loss = 0.6886308193206787
Epoch 20 / 10000, Loss = 0.6878283023834229
Epoch 21 / 10000, Loss = 0.6870297193527222
Epoch 22 / 10000, Loss = 0.6862375736236572
Epoch 23 / 10000, Loss = 0.6854561

Epoch 220 / 10000, Loss = 0.47809988260269165
Epoch 221 / 10000, Loss = 0.477179616689682
Epoch 222 / 10000, Loss = 0.47626805305480957
Epoch 223 / 10000, Loss = 0.47536614537239075
Epoch 224 / 10000, Loss = 0.4744741916656494
Epoch 225 / 10000, Loss = 0.4735901355743408
Epoch 226 / 10000, Loss = 0.4727138876914978
Epoch 227 / 10000, Loss = 0.47184640169143677
Epoch 228 / 10000, Loss = 0.4709881842136383
Epoch 229 / 10000, Loss = 0.4701386094093323
Epoch 230 / 10000, Loss = 0.4692958891391754
Epoch 231 / 10000, Loss = 0.4684595763683319
Epoch 232 / 10000, Loss = 0.46763455867767334
Epoch 233 / 10000, Loss = 0.46681779623031616
Epoch 234 / 10000, Loss = 0.4660084545612335
Epoch 235 / 10000, Loss = 0.46520957350730896
Epoch 236 / 10000, Loss = 0.4644213616847992
Epoch 237 / 10000, Loss = 0.46364545822143555
Epoch 238 / 10000, Loss = 0.4628818929195404
Epoch 239 / 10000, Loss = 0.46213099360466003
Epoch 240 / 10000, Loss = 0.4613904654979706
Epoch 241 / 10000, Loss = 0.4606611132621765
Ep

Epoch 420 / 10000, Loss = 0.40768614411354065
Epoch 421 / 10000, Loss = 0.40755167603492737
Epoch 422 / 10000, Loss = 0.4074177145957947
Epoch 423 / 10000, Loss = 0.40728428959846497
Epoch 424 / 10000, Loss = 0.40715011954307556
Epoch 425 / 10000, Loss = 0.40701597929000854
Epoch 426 / 10000, Loss = 0.4068821370601654
Epoch 427 / 10000, Loss = 0.4067477285861969
Epoch 428 / 10000, Loss = 0.4066145718097687
Epoch 429 / 10000, Loss = 0.40648260712623596
Epoch 430 / 10000, Loss = 0.4063507318496704
Epoch 431 / 10000, Loss = 0.4062196910381317
Epoch 432 / 10000, Loss = 0.40608933568000793
Epoch 433 / 10000, Loss = 0.4059595763683319
Epoch 434 / 10000, Loss = 0.40583157539367676
Epoch 435 / 10000, Loss = 0.40570440888404846
Epoch 436 / 10000, Loss = 0.4055767357349396
Epoch 437 / 10000, Loss = 0.4054492712020874
Epoch 438 / 10000, Loss = 0.405321329832077
Epoch 439 / 10000, Loss = 0.4051932692527771
Epoch 440 / 10000, Loss = 0.4050654470920563
Epoch 441 / 10000, Loss = 0.40493813157081604
E

Epoch 613 / 10000, Loss = 0.3852503001689911
Epoch 614 / 10000, Loss = 0.385139137506485
Epoch 615 / 10000, Loss = 0.385029137134552
Epoch 616 / 10000, Loss = 0.3849206268787384
Epoch 617 / 10000, Loss = 0.38481199741363525
Epoch 618 / 10000, Loss = 0.384703665971756
Epoch 619 / 10000, Loss = 0.38459575176239014
Epoch 620 / 10000, Loss = 0.38448795676231384
Epoch 621 / 10000, Loss = 0.38437917828559875
Epoch 622 / 10000, Loss = 0.3842719495296478
Epoch 623 / 10000, Loss = 0.3841651976108551
Epoch 624 / 10000, Loss = 0.3840583860874176
Epoch 625 / 10000, Loss = 0.3839513063430786
Epoch 626 / 10000, Loss = 0.3838447630405426
Epoch 627 / 10000, Loss = 0.383738249540329
Epoch 628 / 10000, Loss = 0.38363224267959595
Epoch 629 / 10000, Loss = 0.3835259675979614
Epoch 630 / 10000, Loss = 0.38342055678367615
Epoch 631 / 10000, Loss = 0.3833153545856476
Epoch 632 / 10000, Loss = 0.3832102417945862
Epoch 633 / 10000, Loss = 0.3831062316894531
Epoch 634 / 10000, Loss = 0.38300222158432007
Epoch 6

Epoch 801 / 10000, Loss = 0.36484766006469727
Epoch 802 / 10000, Loss = 0.3647259771823883
Epoch 803 / 10000, Loss = 0.3646038770675659
Epoch 804 / 10000, Loss = 0.3644808232784271
Epoch 805 / 10000, Loss = 0.3643570840358734
Epoch 806 / 10000, Loss = 0.36423417925834656
Epoch 807 / 10000, Loss = 0.3641107380390167
Epoch 808 / 10000, Loss = 0.36398640275001526
Epoch 809 / 10000, Loss = 0.36386147141456604
Epoch 810 / 10000, Loss = 0.36373740434646606
Epoch 811 / 10000, Loss = 0.36361265182495117
Epoch 812 / 10000, Loss = 0.3634864091873169
Epoch 813 / 10000, Loss = 0.363361656665802
Epoch 814 / 10000, Loss = 0.363237202167511
Epoch 815 / 10000, Loss = 0.36311039328575134
Epoch 816 / 10000, Loss = 0.3629850447177887
Epoch 817 / 10000, Loss = 0.36285996437072754
Epoch 818 / 10000, Loss = 0.36273449659347534
Epoch 819 / 10000, Loss = 0.36260899901390076
Epoch 820 / 10000, Loss = 0.36248210072517395
Epoch 821 / 10000, Loss = 0.36235588788986206
Epoch 822 / 10000, Loss = 0.3622310161590576


...

Epoch 9094 / 10000, Loss = 0.13833759725093842
Epoch 9095 / 10000, Loss = 0.13854379951953888
Epoch 9096 / 10000, Loss = 0.13857288658618927
Epoch 9097 / 10000, Loss = 0.13862541317939758
Epoch 9098 / 10000, Loss = 0.138491690158844
Epoch 9099 / 10000, Loss = 0.13830898702144623
Epoch 9100 / 10000, Loss = 0.13807858526706696
Epoch 9101 / 10000, Loss = 0.13790567219257355
Epoch 9102 / 10000, Loss = 0.1378118395805359
Epoch 9103 / 10000, Loss = 0.13783566653728485
Epoch 9104 / 10000, Loss = 0.1379421055316925
Epoch 9105 / 10000, Loss = 0.13807356357574463
Epoch 9106 / 10000, Loss = 0.13821737468242645
Epoch 9107 / 10000, Loss = 0.13829384744167328
Epoch 9108 / 10000, Loss = 0.13832922279834747
Epoch 9109 / 10000, Loss = 0.13821087777614594
Epoch 9110 / 10000, Loss = 0.13806547224521637
Epoch 9111 / 10000, Loss = 0.1378956288099289
Epoch 9112 / 10000, Loss = 0.13781338930130005
Epoch 9113 / 10000, Loss = 0.13775865733623505
Epoch 9114 / 10000, Loss = 0.13777391612529755
Epoch 9115 / 10000

Epoch 9283 / 10000, Loss = 0.138055220246315
Epoch 9284 / 10000, Loss = 0.13800813257694244
Epoch 9285 / 10000, Loss = 0.13795597851276398
Epoch 9286 / 10000, Loss = 0.13774718344211578
Epoch 9287 / 10000, Loss = 0.1375291347503662
Epoch 9288 / 10000, Loss = 0.13732756674289703
Epoch 9289 / 10000, Loss = 0.13723592460155487
Epoch 9290 / 10000, Loss = 0.137222558259964
Epoch 9291 / 10000, Loss = 0.13728556036949158
Epoch 9292 / 10000, Loss = 0.13738295435905457
Epoch 9293 / 10000, Loss = 0.13747183978557587
Epoch 9294 / 10000, Loss = 0.13758918642997742
Epoch 9295 / 10000, Loss = 0.1376287192106247
Epoch 9296 / 10000, Loss = 0.1376848667860031
Epoch 9297 / 10000, Loss = 0.1375899463891983
Epoch 9298 / 10000, Loss = 0.13744379580020905
Epoch 9299 / 10000, Loss = 0.13729886710643768
Epoch 9300 / 10000, Loss = 0.13721658289432526
Epoch 9301 / 10000, Loss = 0.13715139031410217
Epoch 9302 / 10000, Loss = 0.13716109097003937
Epoch 9303 / 10000, Loss = 0.13719125092029572
Epoch 9304 / 10000, L

Epoch 9473 / 10000, Loss = 0.13711751997470856
Epoch 9474 / 10000, Loss = 0.13725636899471283
Epoch 9475 / 10000, Loss = 0.137364000082016
Epoch 9476 / 10000, Loss = 0.13740655779838562
Epoch 9477 / 10000, Loss = 0.13749827444553375
Epoch 9478 / 10000, Loss = 0.1374097764492035
Epoch 9479 / 10000, Loss = 0.137335404753685
Epoch 9480 / 10000, Loss = 0.13709059357643127
Epoch 9481 / 10000, Loss = 0.13689905405044556
Epoch 9482 / 10000, Loss = 0.1367029994726181
Epoch 9483 / 10000, Loss = 0.13663537800312042
Epoch 9484 / 10000, Loss = 0.13669626414775848
Epoch 9485 / 10000, Loss = 0.136803537607193
Epoch 9486 / 10000, Loss = 0.13694611191749573
Epoch 9487 / 10000, Loss = 0.1370568871498108
Epoch 9488 / 10000, Loss = 0.13712994754314423
Epoch 9489 / 10000, Loss = 0.13719618320465088
Epoch 9490 / 10000, Loss = 0.1371825784444809
Epoch 9491 / 10000, Loss = 0.1370674967765808
Epoch 9492 / 10000, Loss = 0.13691985607147217
Epoch 9493 / 10000, Loss = 0.13671240210533142
Epoch 9494 / 10000, Loss

Epoch 9681 / 10000, Loss = 0.13623608648777008
Epoch 9682 / 10000, Loss = 0.1361864060163498
Epoch 9683 / 10000, Loss = 0.13614417612552643
Epoch 9684 / 10000, Loss = 0.1360921561717987
Epoch 9685 / 10000, Loss = 0.13606175780296326
Epoch 9686 / 10000, Loss = 0.1360621452331543
Epoch 9687 / 10000, Loss = 0.13604414463043213
Epoch 9688 / 10000, Loss = 0.13606004416942596
Epoch 9689 / 10000, Loss = 0.13606363534927368
Epoch 9690 / 10000, Loss = 0.1360807567834854
Epoch 9691 / 10000, Loss = 0.13610078394412994
Epoch 9692 / 10000, Loss = 0.13612759113311768
Epoch 9693 / 10000, Loss = 0.1361677348613739
Epoch 9694 / 10000, Loss = 0.13625715672969818
Epoch 9695 / 10000, Loss = 0.1363295465707779
Epoch 9696 / 10000, Loss = 0.13648825883865356
Epoch 9697 / 10000, Loss = 0.1366579532623291
Epoch 9698 / 10000, Loss = 0.136902317404747
Epoch 9699 / 10000, Loss = 0.13712045550346375
Epoch 9700 / 10000, Loss = 0.13736501336097717
Epoch 9701 / 10000, Loss = 0.13729047775268555
Epoch 9702 / 10000, Lo

Epoch 9877 / 10000, Loss = 0.1355324536561966
Epoch 9878 / 10000, Loss = 0.13547058403491974
Epoch 9879 / 10000, Loss = 0.13552822172641754
Epoch 9880 / 10000, Loss = 0.13566868007183075
Epoch 9881 / 10000, Loss = 0.1358197033405304
Epoch 9882 / 10000, Loss = 0.13598966598510742
Epoch 9883 / 10000, Loss = 0.1360865980386734
Epoch 9884 / 10000, Loss = 0.1362084150314331
Epoch 9885 / 10000, Loss = 0.13618935644626617
Epoch 9886 / 10000, Loss = 0.1362755447626114
Epoch 9887 / 10000, Loss = 0.13607220351696014
Epoch 9888 / 10000, Loss = 0.13588953018188477
Epoch 9889 / 10000, Loss = 0.1357165277004242
Epoch 9890 / 10000, Loss = 0.13555169105529785
Epoch 9891 / 10000, Loss = 0.13544531166553497
Epoch 9892 / 10000, Loss = 0.13544176518917084
Epoch 9893 / 10000, Loss = 0.13546361029148102
Epoch 9894 / 10000, Loss = 0.1355208456516266
Epoch 9895 / 10000, Loss = 0.13556817173957825
Epoch 9896 / 10000, Loss = 0.13558228313922882
Epoch 9897 / 10000, Loss = 0.13564243912696838
Epoch 9898 / 10000, 

## Symmetric classifier

In [324]:
tf.reset_default_graph()
num_features = good_train.shape[1]

input_left = tf.placeholder(tf.float32, shape=[None, num_features*2])
input_right = tf.concat([input_left[:, num_features:], input_left[:, :num_features]], axis=1)
output = tf.placeholder(tf.float32, shape=[None,1])

f_left = small_network(input_left)
f_right = small_network(input_right)
logit = f_left - f_right

h = tf.sigmoid(logit)

loss = tf.losses.sigmoid_cross_entropy(output, logit)
lr = tf.placeholder(tf.float32, shape=[])
train_op = tf.train.AdamOptimizer(learning_rate=lr, beta1=0.9, beta2=0.999).minimize(loss)

In [325]:
symm_hashmap = {}

def asymmetric_classification(good_data, bad_data, l_r, num_epochs, num_batches, if_test):
    
    bsize_good = len(good_data) // num_batches
    bsize_bad = len(bad_data) // num_batches
    losses = []
    y = np.empty((num_batches * bsize_good * bsize_bad, 1), int)
    y.fill(1)
    
    for epoch in range(num_epochs):
        total_loss = 0.0
        good_data = shuffle(good_data)
        bad_data = shuffle(bad_data)
        h_out = []
            
        for batch in range(num_batches):
            
            y_ = np.empty((bsize_good * bsize_bad, 1), int)
            y_.fill(1.)
            minibatch = []
            
            for i in range(batch * bsize_good, (batch + 1) * bsize_good):
                for j in range(batch * bsize_bad, (batch + 1) * bsize_bad):
                    
                    g = good_data.iloc[i,:].reshape(1,-1)
                    b = bad_data.iloc[j,:].reshape(1,-1)
                    minibatch.append(np.concatenate((g, b), axis=None))
                    
                    if(if_test):
                        hash_good = hashlib.sha512(g.tobytes()).hexdigest()
                        hash_bad = hashlib.sha512(b.tobytes()).hexdigest()
                        key = tuple((hash_good, hash_bad))
                        symm_hashmap[key] = 1
                        
            loss_, h_, _ = sess.run([loss, h, train_op], feed_dict={input_left: minibatch, output: y_, lr: l_r})
            h_out.extend([hh[0] for hh in h_])
            total_loss += loss_

        losses.append(total_loss / num_batches)
        print("Epoch {} / {}, Loss = {}".format(epoch + 1, num_epochs, total_loss / num_batches))
        
    return h_out, y, losses

In [326]:
with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    
    print("Training...")
    symm_train_out, y, losses = asymmetric_classification(good_train, bad_train, 0.0003, 10, 15, False)
    metrics(symm_train_out, y)
    
    print("\nTesting...")
    symm_test_out, y, losses = asymmetric_classification(good_test, bad_test, 0.0003, 1, 1, True)
    metrics(symm_test_out, y)

Training...
Epoch 1 / 10, Loss = 0.6387853821118673
Epoch 2 / 10, Loss = 0.5551133910814922
Epoch 3 / 10, Loss = 0.4746880908807119
Epoch 4 / 10, Loss = 0.40641117095947266
Epoch 5 / 10, Loss = 0.3677889287471771
Epoch 6 / 10, Loss = 0.3491966674725215
Epoch 7 / 10, Loss = 0.3411020894845327
Epoch 8 / 10, Loss = 0.3258523086706797
Epoch 9 / 10, Loss = 0.32931148310502373
Epoch 10 / 10, Loss = 0.32455511192480724

Accuracy score =  0.850149075730471
Precision score =  1.0
Recall score =  0.850149075730471
F1 score =  0.9190060270087343

Testing...
Epoch 1 / 1, Loss = 0.3171299993991852

Accuracy score =  0.8638888888888889
Precision score =  1.0
Recall score =  0.8638888888888889
F1 score =  0.9269746646795828


## Base & symmetric classification comparison

In [327]:
N = len(good_test) * len(bad_test)
a = 0

for i in range(len(good_test)):
    for j in range(len(bad_test)):
        hash_good = hashlib.sha512(good_test.iloc[i,:].values.tobytes()).hexdigest()
        hash_bad = hashlib.sha512(bad_test.iloc[j,:].values.tobytes()).hexdigest()
        key = (hash_good, hash_bad)
        if((base_hashmap[hash_good][1] == 1 and base_hashmap[hash_bad][1] == 0 and symm_hashmap[key] == 1)
          or (base_hashmap[hash_good][1] == 0 and base_hashmap[hash_bad][1] == 1 and symm_hashmap[key] == 0)):
            ## oba klasifikatora su jednako zaključila
            a += 1
        else:
            ## oba klasifikatora nisu zaključila jednako
            print("\n------------------------\nTestni dobar primjer:\n", good_test.iloc[i,:].values, 
                  "\nBase classificator zaključio je da je ovaj primjer: ", base_hashmap[hash_good][1])
            print("\nTestni loš primjer:\n", bad_test.iloc[j,:].values,
                  "\nBase classificator zaključio je da je ovaj primjer: ", base_hashmap[hash_bad][1])
            print("Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš: ",symm_hashmap[key])

print("Ukupno preklapanje u procjenama klasifikatora je: ", a/N)    


------------------------
Testni dobar primjer:
 [-1.54609786  0.47513072  0.48128777  1.86652569  1.67645028  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0

Testni loš primjer:
 [ 0.84191642 -0.22372084 -0.47908676 -0.4449995  -0.47628387  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-1.54609786  0.47513072  0.48128777  1.86652569  1.67645028  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0

Testni loš primjer:
 [-1.54609786  0.47513072 -0.47908676 -0.4449995  -0.0312511   1.
  0.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

-------


Testni loš primjer:
 [-1.54609786 -0.14607067  0.48128777 -0.4449995   0.94501468  0.
  1.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -1.69907414  0.48128777  0.71076309  0.06679389  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [-0.35209072  0.94103176 -0.47908676 -0.4449995  -0.39241739  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -1.69907414  0.48128777  0.71076309  0.06679389  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni 

 [ 8.41916418e-01 -5.51737667e-16 -4.79086761e-01 -4.44999502e-01
 -4.93927255e-01  0.00000000e+00  1.00000000e+00  0.00000000e+00
  1.00000000e+00  0.00000000e+00] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -1.69907414  0.48128777  0.71076309  0.06679389  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [ 0.84191642 -2.16497518  0.48128777  0.71076309 -0.25296218  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -1.69907414  0.48128777  0.71076309  0.06679389  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je

 [-1.54609786  0.08687985 -0.47908676  1.86652569  2.54395743  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0

Testni loš primjer:
 [-1.54609786 -0.37902119  0.48128777  1.86652569  2.28647622  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-1.54609786  0.08687985 -0.47908676  1.86652569  2.54395743  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0

Testni loš primjer:
 [ 0.84191642  0.47513072 -0.47908676 -0.4449995  -0.64377515  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-1.546


------------------------
Testni dobar primjer:
 [-1.54609786 -0.68962188 -0.47908676  0.71076309  0.54300469  0.
  1.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0

Testni loš primjer:
 [ 0.84191642 -0.06842049  0.48128777  0.71076309 -0.44148049  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-1.54609786 -0.68962188 -0.47908676  0.71076309  0.54300469  0.
  1.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0

Testni loš primjer:
 [-0.35209072 -0.06842049  0.48128777 -0.4449995  -0.14105964  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

-------

...

Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [ 0.84191642  0.47513072  0.48128777 -0.4449995  -0.30734246  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [-1.54609786 -0.45667136  0.48128777 -0.4449995   0.51633757  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [ 0.84191642  0.47513072  0.48128777 -0.4449995  -0.30734246  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [ 0.84191642 -0.68962188  0.48128777 -0.4449995  -0.51817748  0.
  1.          0.          0.          1.        ] 
Base cla

Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [ 0.84191642  0.47513072  0.48128777 -0.4449995  -0.30734246  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [ 8.41916418e-01 -5.51737667e-16  4.81287772e-01  1.86652569e+00
 -1.90364428e-01  0.00000000e+00  1.00000000e+00  0.00000000e+00
  0.00000000e+00  1.00000000e+00] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [ 0.84191642  0.47513072  0.48128777 -0.4449995  -0.30734246  1.
  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [ 0.84191642  0.00922968 -0.47908676 -0.4449995  -0.50399703  0.
  1.      

Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -0.76727205 -0.47908676 -0.4449995  -0.37574077  0.
  1.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [-0.35209072 -0.68962188  0.48128777 -0.4449995  -0.42142021  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -0.76727205 -0.47908676 -0.4449995  -0.37574077  0.
  1.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [-1.54609786  0.94103176 -0.47908676 -0.4449995  -0.13042527  0.
  1.          0.          0.          1.        ] 
Base cla

  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -0.76727205 -0.47908676 -0.4449995  -0.37574077  0.
  1.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [-0.35209072  0.08687985  0.48128777  0.71076309 -0.13622583  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-0.35209072 -0.76727205 -0.47908676 -0.4449995  -0.37574077  0.
  1.          1.          0.          0.        ] 
Base classificator zaključio je da je ovaj primjer:  0.0

Testni loš primjer:
 [ 0.84191642 -0.9225724  -0.47908676 -0.4449995  -0.49392726  0.
  1.    

  0.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-1.54609786e+00 -5.51737667e-16  4.81287772e-01 -4.44999502e-01
  1.94037592e+00  1.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  1.00000000e+00] 
Base classificator zaključio je da je ovaj primjer:  1.0

Testni loš primjer:
 [ 0.84191642  0.47513072 -0.47908676 -0.4449995  -0.64377515  0.
  1.          0.          0.          1.        ] 
Base classificator zaključio je da je ovaj primjer:  1.0
Symmetric classificator zaključio je da je prvi primjer dobar, a drugi loš:  1

------------------------
Testni dobar primjer:
 [-1.54609786e+00 -5.51737667e-16  4.81287772e-01 -4.44999502e-01
  1.94037592e+00  1.00000000e+00  0.00000000e+00  0.00000000e+00
  0.00000000e+00  1.00000000e+00] 
Base classificator zaključio je da je ovaj primjer:  1